# Assignment 7: Backpropagation
Read the Rojas book (https://page.mi.fu-berlin.de/rojas/neural/neuron.pdf), chapter 7.3.3 and learn about the "matrix way" of implementing backprop. 

## Ex. 7.1 XOR
Implement a two-layer artificial neural network with two input neurons and one output neuron. Choose the number of hidden neurons to your liking and add an error "neuron" to your network. Our goal is to learn the XOR function. What does the network return for random weights of all combinations of (binary) inputs? **(RESULT)**

## Ex. 7.2 Backpropagation
Implement Backpropagation and optimize the weights of your neural network using the XOR training set: 

#### x, y

(0,0), 0 

(0,1), 1

(1,0), 1

(1,1), 0

How many training iterations do you need? Plot the network error over the number of iterations! **(RESULT)**

In [2]:
import numpy as np
import math


def sigmoid_derivative(p):
    return p * (1 - p)

#file neuralNetwork.py
# input is only normal arrays please.
class NrlNtrk:
    
    def __init__(self, ftrsSz, clsCnt, bias, hdnLrsShps, bp=False):
        self.bp = bp
        self.bias = bias
        self.lrs = [np.random.rand(i[0] + bias, i[1]) for i in hdnLrsShps]
        self.lrs.append(np.random.rand(self.lrs[-1].shape[1] + bias, clsCnt))
        self.__sgmd = lambda x: 1 / (1 + np.e ** -x)
        self.__d = lambda x: x * (1 - x)

    def __rr(self, x, y):
        arr = []
        for i in range (0,len(x)): 
            arr.append( math.pow(y[i]-x[i], 1))
        return np.array(arr, ndmin = 2).T
    
    def __gtTpts(self, ftr):
        tpts = []
        y = np.array(ftr, ndmin=2).T #T here doesn't transpose but get original, because input vector is treated as col.
        for lr in self.lrs:
            tpts.append(self.__sgmd(np.dot(lr.T, y)))
            y = np.array(np.append(tpts[-1], 1), ndmin=2).T 
        return tpts
    def __bpInter(self, rr, tpts, ftr):
        
        ftr = np.array(ftr, ndmin=2).T
        nls = []
        nls.append(self.lrs[1] + np.dot(np.array([np.append(tpts[-2].T, 1)]).T, (2*(rr) * sigmoid_derivative(tpts[-1]))))
        
        for i in range(len(self.lrs)-2, 0, -1):
            nls.append(self.lrs[i] + np.dot(np.array([np.append(tpts[i-1].T, 1)]).T, (2*(rr) * sigmoid_derivative(tpts[i]))))
                
 #       d_weights2 = np.dot(self.layer1.T, (2*(self.y - self.output) * sigmoid_derivative(self.output)))
  #      d_weights1 = np.dot(self.input.T,  (np.dot(2*(self.y - self.output) * sigmoid_derivative(self.output), self.weights2.T) * sigmoid_derivative(self.layer1)))
   
        nls.append(self.lrs[0] + np.dot(ftr,  (np.dot(2*rr * sigmoid_derivative(tpts[-1]), self.lrs[1][:][:-1].T) * sigmoid_derivative(tpts[0]).T)))
        
        self.lrs = list(reversed(nls))
        
    def __bp(self, rr, tpts, ftr):
        cnst = -0.4
        nlrs = []      
        g = rr * tpts[-1] * (1.0 - tpts[-1].T)
        nlrs.append(self.lrs[-1] + (cnst * np.dot(g, np.array(np.append(tpts[-2], 1), ndmin = 2))).T)
        for i in range(len(self.lrs)-2, 0, -1):
            print("Inner layers")
            d = np.diag((tpts[i] * (1 - tpts[i])).T[0])
            g = np.dot(np.dot(d, self.lrs[i+1][:][:-1]), g)
     
            nlrs.append(self.lrs[i] + (cnst * np.dot(g, np.array(np.append(tpts[i-1], 1), ndmin = 2))).T)
        
        d = np.diag((tpts[0] * (1 - tpts[0])).T[0])
        g = np.dot(np.dot(d, self.lrs[1][:][:-1]), g)
        nlrs.append(self.lrs[0] + (cnst * np.dot(g, np.array(ftr, ndmin = 2))).T) 

        self.lrs = list(reversed(nlrs))
    def predict(self, ftrs):
        for (x, r) in enumerate(ftrs):
            k = r.copy()
            if(self.bias !=0): k.append(1)
            tpts = self.__gtTpts(k)
            #print("result")
            #print(ftr)
            #print(tpts[-1])
    
    def train(self, ftrs, clsss):
        #move to validation ToDo
        #if isinstance(clsss, np.ndarray) == False:
        #    clsss = np.array(clsss, dtype=float)
        for we in range(0,1):
            for (x, r) in enumerate(ftrs):
                k = r.copy()
                if(self.bias !=0): k.append(1)
                #Start of numpyfying    
                tpts = self.__gtTpts(k)
                rr = self.__rr(tpts[-1].T, np.array(clsss[x], ndmin=2).T)  
           #     print("Input:", )
           #     print(k[:-1])
           #     print("Result")
           #     print(tpts[-1].T)
                if(self.bp):
                    self.__bpInter(rr, tpts, k)
                #pdtLrs(tpts, rr)
          #  print(ftrs) 
trainSet = [[1,0],[0,0],[1,1],[0,1]]
trainSetClasses = [[1],[0],[0],[1]]

#Input features size
#Output class size
#Bias
#hidden layers shapes (2x4)(4x2)(2x22)
neuralNetwork = NrlNtrk(2, 1, 1, [[2,10]])
neuralNetwork.train(trainSet, trainSetClasses)            
#neuralNetwork.predict(trainSet)


Input:
[1, 0]
Result
[[0.98618925]]
Input:
[0, 0]
Result
[[0.97897264]]
Input:
[1, 1]
Result
[[0.9900165]]
Input:
[0, 1]
Result
[[0.9856896]]


In [114]:
import numpy as np
import math
from mlxtend.data import loadlocal_mnist

X, y = loadlocal_mnist(
        images_path='images/nn/train-images.idx3-ubyte', 
        labels_path='images/nn/train-labels.idx1-ubyte')
X= X.tolist()
y = y.tolist()
yDecoded = []
for i in y:
    sy = [0 for i in range(0,10)]
    sy[i] = 1
    yDecoded.append(sy)
y = yDecoded

def sigmoid_derivative(p):
    return p * (1 - p)
def calcD(o):#, o2, o1):
    # create d matrix
    d = np.zeros((o.shape[0], o.shape[0]))
    for j in range(len(o)):
        oi2 = o[j]
        d[j, j] = sigmoid_derivative(oi2) * (1 - sigmoid_derivative(oi2))
    return d

#file neuralNetwork.py
# input is only normal arrays please.
class NrlNtrk:
    
    def __init__(self, ftrsSz, clsCnt, bs, hdnLrsShps, bp=True):
        self.bp = bp
        self.bs = bs
        self.lrs = [np.random.rand(i[0] + bs, i[1]) for i in hdnLrsShps]
        self.lrs.append(np.random.rand(self.lrs[-1].shape[1] + bs, clsCnt))
        self.__sgmd = lambda x: 1 / (1 + np.e ** -x)
        self.__d = lambda x: x * (1 - x)

    def __rr(self, x, y):
       # arr = []
       # for i in range (0,len(y)):
        #    arr.append( math.pow(y[i]-x.T[i], 1))
        return x-y
    
    def __gtTpts(self, ftr):
        tpts = []
        y = np.array(ftr, ndmin=2).T #T here doesn't transpose but get original, because input vector is treated as col.
        for lr in self.lrs:
            tpts.append(self.__sgmd(np.dot(lr.T, y)))
            if(self.bs ==1) : y = np.array(np.append(tpts[-1], 1), ndmin=2).T 
            else: y = tpts[-1]    
        return tpts
    def __bpInter(self, rr, tpts, ftr):
        
        ftr = np.array(ftr, ndmin=2).T
        nls = []
        c = 1
        #brd = (c* np.dot(calcD(tpts[-1]), rr))
        #nls.append(self.lrs[-1] + np.dot(brd, np.array([np.append(tpts[-2].T, 1)])).T)
            
#        for i in range(len(self.lrs)-2 ,0, -1):
#            brd = np.dot(brd, self.lrs[i+1][:-self.bs].T) * sigmoid_derivative(tpts[i]).T
#            nls.append(self.lrs[i] + np.dot(np.array([np.append(tpts[i-1].T, 1)]).T, brd))
                
 #       d_weights2 = np.dot(self.layer1.T, (2*(self.y - self.output) * sigmoid_derivative(self.output)))
  #      d_weights1 = np.dot(self.input.T,  (np.dot(2*(self.y - self.output) * sigmoid_derivative(self.output), self.weights2.T) * sigmoid_derivative(self.layer1)))
       # brd = np.dot(brd, self.lrs[2][:-1].T) * sigmoid_derivative(tpts[1]).T
        #nls.append(self.lrs[1] + np.dot(np.array([np.append(tpts[0].T, 1)]).T, brd))
                
        #lrerr = np.dot(brd)
        #ldel = np.dot(calcD(tpts[0]), lrerr)
        #nls.append(self.lrs[0] + np.dot(ldel,ftr).T)
        
        d_weights2 = np.dot(self.lrs[-1], (2*(rr) * sigmoid_derivative(tpts[-1])))
        #d_weights1 = np.dot(ftr.T,  (np.dot(2*(rr) * sigmoid_derivative(tpts[-1]).T, self.lrs[-1][:][:-self.bs].T) * sigmoid_derivative(tpts[0])))
        print( (2*rr * sigmoid_derivative(tpts[-1])).shape)
        d_weights1 = np.dot(ftr,  (np.dot((2*rr * sigmoid_derivative(tpts[-1])).T, self.lrs[1][:][:-1].T) * sigmoid_derivative(tpts[0]).T))

        self.lrs[-1] += d_weights2
        self.lrs[0] += d_weights1
        
        #nls.append(self.lrs[0] + np.dot( np.dot(np.dot(calcD(tpts[0]), self.lrs[1][:][:-self.bs]),brd), ftr.T).T)
        
        #self.lrs = list(reversed(nls))
        
    def predict(self, ftrs):
        for (x, r) in enumerate(ftrs):
            k = r.copy()
            if(self.bs !=0): k.append(1)
            tpts = self.__gtTpts(k)
            #print("result")
            #print(ftr)
            #print(tpts[-1])
    
    def train(self, ftrs, clsss):
        #move to validation ToDo
        #if isinstance(clsss, np.ndarray) == False:
        #    clsss = np.array(clsss, dtype=float)
        for we in range(0,12500):
            for (x, r) in enumerate(ftrs):
                k = r.copy()
                if(self.bs !=0): k.append(1)
                #Start of numpyfying    
                tpts = self.__gtTpts(k)
                rr = self.__rr(tpts[-1], np.array(clsss[x], ndmin=2).T)
                #print(k)
                if(True):
                    print("err")
                    print(rr)
                    print("Result")
                    print(tpts[-1].T)
                    print("should")
                    print(np.array(clsss[x], ndmin=2).T)
                if(self.bp):
                        self.__bpInter(rr, tpts, k)
                #pdtLrs(tpts, rr)
          #  print(ftrs) 
trainSet = [[1,0],[0,0],[1,1],[0,1]]
trainSetClasses = [[1],[0],[0],[1]]

#Input features size
#Output class size
#Bias
#hidden layers shapes (2x4)(4x2)(2x22)
neuralNetwork = NrlNtrk(2, 1, 1, [[2,20]])
neuralNetwork.train(trainSet, trainSetClasses)            
neuralNetwork.predict(trainSet)

#neuralNetwork = NrlNtrk(2, 10, 1, [[784,40]])
#neuralNetwork.train(X, y) 
#neuralNetwork.predict(y)
# class input adapter:
    #class init imageVectors.
    # read image.
    # return flattened vector

def train(ftrs, cls):
    return 'manar'
    # while result of network is not cls keep updating weights.
    # updating weights:
        # let first layer calculate ftrs.
        # first layer 
# train
    #inputs: flattened image(train vector), feature
    
#Function takes object
def adaptInput():
    return 'manar'
# predict
    #inputs: 

err
[[-0.00070155]]
Result
[[0.99929845]]
should
[[1]]
(1, 1)
err
[[0.99832603]]
Result
[[0.99832603]]
should
[[0]]
(1, 1)
err
[[0.99966452]]
Result
[[0.99966452]]
should
[[0]]
(1, 1)
err
[[-0.00065413]]
Result
[[0.99934587]]
should
[[1]]
(1, 1)
err
[[-0.00068082]]
Result
[[0.99931918]]
should
[[1]]
(1, 1)
err
[[0.9983699]]
Result
[[0.9983699]]
should
[[0]]
(1, 1)
err
[[0.99967512]]
Result
[[0.99967512]]
should
[[0]]
(1, 1)
err
[[-0.00063514]]
Result
[[0.99936486]]
should
[[1]]
(1, 1)
err
[[-0.00066116]]
Result
[[0.99933884]]
should
[[1]]
(1, 1)
err
[[0.99841167]]
Result
[[0.99841167]]
should
[[0]]
(1, 1)
err
[[0.99968516]]
Result
[[0.99968516]]
should
[[0]]
(1, 1)
err
[[-0.00061711]]
Result
[[0.99938289]]
should
[[1]]
(1, 1)
err
[[-0.00064249]]
Result
[[0.99935751]]
should
[[1]]
(1, 1)
err
[[0.99845146]]
Result
[[0.99845146]]
should
[[0]]
(1, 1)
err
[[0.99969467]]
Result
[[0.99969467]]
should
[[0]]
(1, 1)
err
[[-0.00059997]]
Result
[[0.99940003]]
should
[[1]]
(1, 1)
err
[[-0.00062473]

(1, 1)
err
[[0.9998722]]
Result
[[0.9998722]]
should
[[0]]
(1, 1)
err
[[-0.00026924]]
Result
[[0.99973076]]
should
[[1]]
(1, 1)
err
[[-0.00028153]]
Result
[[0.99971847]]
should
[[1]]
(1, 1)
err
[[0.99925511]]
Result
[[0.99925511]]
should
[[0]]
(1, 1)
err
[[0.99987423]]
Result
[[0.99987423]]
should
[[0]]
(1, 1)
err
[[-0.00026529]]
Result
[[0.99973471]]
should
[[1]]
(1, 1)
err
[[-0.00027742]]
Result
[[0.99972258]]
should
[[1]]
(1, 1)
err
[[0.99926477]]
Result
[[0.99926477]]
should
[[0]]
(1, 1)
err
[[0.99987621]]
Result
[[0.99987621]]
should
[[0]]
(1, 1)
err
[[-0.00026144]]
Result
[[0.99973856]]
should
[[1]]
(1, 1)
err
[[-0.00027342]]
Result
[[0.99972658]]
should
[[1]]
(1, 1)
err
[[0.9992742]]
Result
[[0.9992742]]
should
[[0]]
(1, 1)
err
[[0.99987813]]
Result
[[0.99987813]]
should
[[0]]
(1, 1)
err
[[-0.00025769]]
Result
[[0.99974231]]
should
[[1]]
(1, 1)
err
[[-0.00026952]]
Result
[[0.99973048]]
should
[[1]]
(1, 1)
err
[[0.9992834]]
Result
[[0.9992834]]
should
[[0]]
(1, 1)
err
[[0.99988]]

[[0.99948847]]
should
[[0]]
(1, 1)
err
[[0.9999203]]
Result
[[0.9999203]]
should
[[0]]
(1, 1)
err
[[-0.00017414]]
Result
[[0.99982586]]
should
[[1]]
(1, 1)
err
[[-0.0001825]]
Result
[[0.9998175]]
should
[[1]]
(1, 1)
err
[[0.99949323]]
Result
[[0.99949323]]
should
[[0]]
(1, 1)
err
[[0.9999212]]
Result
[[0.9999212]]
should
[[0]]
(1, 1)
err
[[-0.00017233]]
Result
[[0.99982767]]
should
[[1]]
(1, 1)
err
[[-0.00018061]]
Result
[[0.99981939]]
should
[[1]]
(1, 1)
err
[[0.99949791]]
Result
[[0.99949791]]
should
[[0]]
(1, 1)
err
[[0.99992208]]
Result
[[0.99992208]]
should
[[0]]
(1, 1)
err
[[-0.00017055]]
Result
[[0.99982945]]
should
[[1]]
(1, 1)
err
[[-0.00017875]]
Result
[[0.99982125]]
should
[[1]]
(1, 1)
err
[[0.99950251]]
Result
[[0.99950251]]
should
[[0]]
(1, 1)
err
[[0.99992295]]
Result
[[0.99992295]]
should
[[0]]
(1, 1)
err
[[-0.0001688]]
Result
[[0.9998312]]
should
[[1]]
(1, 1)
err
[[-0.00017693]]
Result
[[0.99982307]]
should
[[1]]
(1, 1)
err
[[0.99950702]]
Result
[[0.99950702]]
should
[[

err
[[-0.00012051]]
Result
[[0.99987949]]
should
[[1]]
(1, 1)
err
[[0.99964971]]
Result
[[0.99964971]]
should
[[0]]
(1, 1)
err
[[0.99994967]]
Result
[[0.99994967]]
should
[[0]]
(1, 1)
err
[[-0.00011388]]
Result
[[0.99988612]]
should
[[1]]
(1, 1)
err
[[-0.00011961]]
Result
[[0.99988039]]
should
[[1]]
(1, 1)
err
[[0.99965204]]
Result
[[0.99965204]]
should
[[0]]
(1, 1)
err
[[0.99995008]]
Result
[[0.99995008]]
should
[[0]]
(1, 1)
err
[[-0.00011303]]
Result
[[0.99988697]]
should
[[1]]
(1, 1)
err
[[-0.00011872]]
Result
[[0.99988128]]
should
[[1]]
(1, 1)
err
[[0.99965434]]
Result
[[0.99965434]]
should
[[0]]
(1, 1)
err
[[0.99995048]]
Result
[[0.99995048]]
should
[[0]]
(1, 1)
err
[[-0.00011219]]
Result
[[0.99988781]]
should
[[1]]
(1, 1)
err
[[-0.00011784]]
Result
[[0.99988216]]
should
[[1]]
(1, 1)
err
[[0.99965661]]
Result
[[0.99965661]]
should
[[0]]
(1, 1)
err
[[0.99995087]]
Result
[[0.99995087]]
should
[[0]]
(1, 1)
err
[[-0.00011137]]
Result
[[0.99988863]]
should
[[1]]
(1, 1)
err
[[-0.0001169

err
[[0.99996535]]
Result
[[0.99996535]]
should
[[0]]
(1, 1)
err
[[-8.06143206e-05]]
Result
[[0.99991939]]
should
[[1]]
(1, 1)
err
[[-8.48194592e-05]]
Result
[[0.99991518]]
should
[[1]]
(1, 1)
err
[[0.9997438]]
Result
[[0.9997438]]
should
[[0]]
(1, 1)
err
[[0.99996557]]
Result
[[0.99996557]]
should
[[0]]
(1, 1)
err
[[-8.01575893e-05]]
Result
[[0.99991984]]
should
[[1]]
(1, 1)
err
[[-8.43413605e-05]]
Result
[[0.99991566]]
should
[[1]]
(1, 1)
err
[[0.99974509]]
Result
[[0.99974509]]
should
[[0]]
(1, 1)
err
[[0.99996578]]
Result
[[0.99996578]]
should
[[0]]
(1, 1)
err
[[-7.97054983e-05]]
Result
[[0.99992029]]
should
[[1]]
(1, 1)
err
[[-8.38681054e-05]]
Result
[[0.99991613]]
should
[[1]]
(1, 1)
err
[[0.99974636]]
Result
[[0.99974636]]
should
[[0]]
(1, 1)
err
[[0.99996598]]
Result
[[0.99996598]]
should
[[0]]
(1, 1)
err
[[-7.92579801e-05]]
Result
[[0.99992074]]
should
[[1]]
(1, 1)
err
[[-8.33996234e-05]]
Result
[[0.9999166]]
should
[[1]]
(1, 1)
err
[[0.99974763]]
Result
[[0.99974763]]
should


...

err
[[0.99999681]]
Result
[[0.99999681]]
should
[[0]]
(1, 1)
err
[[0.99999982]]
Result
[[0.99999982]]
should
[[0]]
(1, 1)
err
[[-5.91023004e-07]]
Result
[[0.99999941]]
should
[[1]]
(1, 1)
err
[[-6.37384454e-07]]
Result
[[0.99999936]]
should
[[1]]
(1, 1)
err
[[0.99999682]]
Result
[[0.99999682]]
should
[[0]]
(1, 1)
err
[[0.99999982]]
Result
[[0.99999982]]
should
[[0]]
(1, 1)
err
[[-5.90963156e-07]]
Result
[[0.99999941]]
should
[[1]]
(1, 1)
err
[[-6.37320228e-07]]
Result
[[0.99999936]]
should
[[1]]
(1, 1)
err
[[0.99999682]]
Result
[[0.99999682]]
should
[[0]]
(1, 1)
err
[[0.99999982]]
Result
[[0.99999982]]
should
[[0]]
(1, 1)
err
[[-5.90903319e-07]]
Result
[[0.99999941]]
should
[[1]]
(1, 1)
err
[[-6.37256015e-07]]
Result
[[0.99999936]]
should
[[1]]
(1, 1)
err
[[0.99999682]]
Result
[[0.99999682]]
should
[[0]]
(1, 1)
err
[[0.99999982]]
Result
[[0.99999982]]
should
[[0]]
(1, 1)
err
[[-5.90843493e-07]]
Result
[[0.99999941]]
should
[[1]]
(1, 1)
err
[[-6.37191813e-07]]
Result
[[0.99999936]]
shou

err
[[0.99999683]]
Result
[[0.99999683]]
should
[[0]]
(1, 1)
err
[[0.99999982]]
Result
[[0.99999982]]
should
[[0]]
(1, 1)
err
[[-5.87866325e-07]]
Result
[[0.99999941]]
should
[[1]]
(1, 1)
err
[[-6.33996838e-07]]
Result
[[0.99999937]]
should
[[1]]
(1, 1)
err
[[0.99999683]]
Result
[[0.99999683]]
should
[[0]]
(1, 1)
err
[[0.99999982]]
Result
[[0.99999982]]
should
[[0]]
(1, 1)
err
[[-5.87807062e-07]]
Result
[[0.99999941]]
should
[[1]]
(1, 1)
err
[[-6.33933239e-07]]
Result
[[0.99999937]]
should
[[1]]
(1, 1)
err
[[0.99999683]]
Result
[[0.99999683]]
should
[[0]]
(1, 1)
err
[[0.99999982]]
Result
[[0.99999982]]
should
[[0]]
(1, 1)
err
[[-5.87747811e-07]]
Result
[[0.99999941]]
should
[[1]]
(1, 1)
err
[[-6.33869652e-07]]
Result
[[0.99999937]]
should
[[1]]
(1, 1)
err
[[0.99999683]]
Result
[[0.99999683]]
should
[[0]]
(1, 1)
err
[[0.99999982]]
Result
[[0.99999982]]
should
[[0]]
(1, 1)
err
[[-5.8768857e-07]]
Result
[[0.99999941]]
should
[[1]]
(1, 1)
err
[[-6.33806076e-07]]
Result
[[0.99999937]]
shoul

err
[[-6.30642195e-07]]
Result
[[0.99999937]]
should
[[1]]
(1, 1)
err
[[0.99999685]]
Result
[[0.99999685]]
should
[[0]]
(1, 1)
err
[[0.99999983]]
Result
[[0.99999983]]
should
[[0]]
(1, 1)
err
[[-5.84681768e-07]]
Result
[[0.99999942]]
should
[[1]]
(1, 1)
err
[[-6.30579213e-07]]
Result
[[0.99999937]]
should
[[1]]
(1, 1)
err
[[0.99999685]]
Result
[[0.99999685]]
should
[[0]]
(1, 1)
err
[[0.99999983]]
Result
[[0.99999983]]
should
[[0]]
(1, 1)
err
[[-5.84623094e-07]]
Result
[[0.99999942]]
should
[[1]]
(1, 1)
err
[[-6.30516244e-07]]
Result
[[0.99999937]]
should
[[1]]
(1, 1)
err
[[0.99999685]]
Result
[[0.99999685]]
should
[[0]]
(1, 1)
err
[[0.99999983]]
Result
[[0.99999983]]
should
[[0]]
(1, 1)
err
[[-5.8456443e-07]]
Result
[[0.99999942]]
should
[[1]]
(1, 1)
err
[[-6.30453286e-07]]
Result
[[0.99999937]]
should
[[1]]
(1, 1)
err
[[0.99999685]]
Result
[[0.99999685]]
should
[[0]]
(1, 1)
err
[[0.99999983]]
Result
[[0.99999983]]
should
[[0]]
(1, 1)
err
[[-5.84505777e-07]]
Result
[[0.99999942]]
shoul

[[0.99999983]]
should
[[0]]
(1, 1)
err
[[-5.81470638e-07]]
Result
[[0.99999942]]
should
[[1]]
(1, 1)
err
[[-6.27132977e-07]]
Result
[[0.99999937]]
should
[[1]]
(1, 1)
err
[[0.99999686]]
Result
[[0.99999686]]
should
[[0]]
(1, 1)
err
[[0.99999983]]
Result
[[0.99999983]]
should
[[0]]
(1, 1)
err
[[-5.81412554e-07]]
Result
[[0.99999942]]
should
[[1]]
(1, 1)
err
[[-6.27070639e-07]]
Result
[[0.99999937]]
should
[[1]]
(1, 1)
err
[[0.99999686]]
Result
[[0.99999686]]
should
[[0]]
(1, 1)
err
[[0.99999983]]
Result
[[0.99999983]]
should
[[0]]
(1, 1)
err
[[-5.8135448e-07]]
Result
[[0.99999942]]
should
[[1]]
(1, 1)
err
[[-6.27008312e-07]]
Result
[[0.99999937]]
should
[[1]]
(1, 1)
err
[[0.99999686]]
Result
[[0.99999686]]
should
[[0]]
(1, 1)
err
[[0.99999983]]
Result
[[0.99999983]]
should
[[0]]
(1, 1)
err
[[-5.81296417e-07]]
Result
[[0.99999942]]
should
[[1]]
(1, 1)
err
[[-6.26945997e-07]]
Result
[[0.99999937]]
should
[[1]]
(1, 1)
err
[[0.99999686]]
Result
[[0.99999686]]
should
[[0]]
(1, 1)
err
[[0.999

KeyboardInterrupt: 

# Ex. 7.3 MNIST (BONUS)
Train your network on the [MNIST dataset](http://yann.lecun.com/exdb/mnist/) and state the model accuracy (or the model error) for the training and test sets. **(RESULT)** Compare to this [list](https://rodrigob.github.io/are_we_there_yet/build/classification_datasets_results.html#4d4e495354)


In [27]:
import numpy as np
import math

from mlxtend.data import loadlocal_mnist

X, y = loadlocal_mnist(
        images_path='images/nn/train-images.idx3-ubyte', 
        labels_path='images/nn/train-labels.idx1-ubyte')
X= X.tolist()
y = y.tolist()
yDecoded = []
for i in y:
    sy = [0 for i in range(0,10)]
    sy[i] = 1
    yDecoded.append(sy)
y = yDecoded

def ddns(X):
    if len(X.shape) == 1:
        return np.hstack((X, np.ones(1)))
    else:
        return np.concatenate((X, np.ones((len(X), 1))), axis=1)
def rmvns(X):
    return X[:-1, :]

class GradientDescent:
    def __init__(self):
        self.learning_rate = 0.01
        
    def __call__(self, weights, gradients):
        return [w - self.learning_rate * g for w,g in zip(weights, gradients)]



def sigmoid_derivative(p):
    return p * (1 - p)

#file neuralNetwork.py
# input is only normal arrays please.
class NrlNtrk:
    
    def __init__(self, ftrsSz, clsCnt, bias, hdnLrsShps, bp=True):
        self.bp = bp
        self.bias = bias
        self.lrs = [np.random.rand(i[0] + bias, i[1]) for i in hdnLrsShps]
        self.lrs.append(np.random.rand(self.lrs[-1].shape[1] + bias, clsCnt))
        self.__sgmd = lambda x: 1 / (1 + np.e ** -x)
        self.__d = lambda x: x * (1 - x)
    #col vector
    def __clcD(self,x):
        # create d matrix
        d = np.zeros((x.shape[0], x.shape[0]))
        for j in range(len(x)):
            oi2 = x[j]
            #self.d[j, j] = oi2 * (1 - oi2)
            d[j, j] = sigmoid_derivative(oi2) * (1 - sigmoid_derivative(oi2))
        return d
    
    def __rr(self, x, y):
        arr = []
        for i in range (0,len(x)): 
            arr.append( math.pow(x[i]-y[i], 1))
        return np.array(arr, ndmin = 2).T
    
    def __gtTpts(self, ftr):
        Os = [ftr]
        O_last = ftr
        
        for Wi in self.lrs:
            O_hat = ddns(O_last)
            O_last = self.__sgmd(O_hat.dot(Wi))
            Os.append(O_last)
            
        return Os
    
    def __bpInter(self, rr, tpts, ftr):
        
        ftr = np.array(ftr, ndmin=2).T
        nls = []
#        nls.append(self.lrs[1] + np.dot(np.array([np.append(tpts[-2].T, 1)]).T, (0.1*(rr) * sigmoid_derivative(tpts[-1])).T))
        g1 = 1*np.dot(self.__clcD(sigmoid_derivative(tpts[-1])), rr)
        lr1delta = np.dot(g1, np.array([np.append(tpts[-2].T, 1)]))
        nls.append(self.lrs[1] + lr1delta.T)
    #    for i in range(len(self.lrs)-2, 0, -1):
    #        nls.append(self.lrs[i] + np.dot(np.array([np.append(tpts[i-1].T, 1)]).T, (2*(rr) * sigmoid_derivative(tpts[i]))))
                
 #       d_weights2 = np.dot(self.layer1.T, (2*(self.y - self.output) * sigmoid_derivative(self.output)))
  #      d_weights1 = np.dot(self.input.T,  (np.dot(2*(self.y - self.output) * sigmoid_derivative(self.output), self.weights2.T) * sigmoid_derivative(self.layer1)))
        dw = np.dot(self.__clcD(sigmoid_derivative(tpts[-2])), self.lrs[-1][:][:-1])
        g2 = np.dot(dw,g1)
        lr2delta = np.dot(g2, ftr.T)
        nls.append(self.lrs[0] + lr2delta.T)
#        nls.append(self.lrs[0] + np.dot(ftr,  (np.dot((0.1*rr * sigmoid_derivative(tpts[-1])).T, self.lrs[1][:][:-1].T) * sigmoid_derivative(tpts[0]).T)))
        
        self.lrs = list(reversed(nls))
        
    def __bpSingle(self, rr, tpts, ftr):
        nls = []
        o = tpts[-1]
        op = tpts[-2]
        dlt = o * (1-o) * rr
        nls.append(np.outer(ddons(op.T).T, dlt))

        o = tpts[-2]
        dlt = (o *(1-o)) * (rmvons(self.lrs[-1]).dot(dlt))
        dlt = np.outer(ftr, dlt)
        nls.append(dlt) 
        
    # for o, o_prev, W in zip(tpts[-2::-1], tpts[-3::-1], self.lrs[-1::-1]):
      #      dlt = (o * (1 - o)) * (rmvons(W).dot(delta))
     #       print(w)
    #        nls.append(np.outer(ddons(o_prev), delta))
        nls.reverse()
        
        gr = GradientDescent();
        self.lrs = gr(self.lrs, nls)
        
    def predict(self, ftrs):
        for (x, r) in enumerate(ftrs):
            k = r.copy()
            if(self.bias !=0): k.append(1)
            tpts = self.__gtTpts(k)
            #print("result")
            #print(ftr)
            #print(tpts[-1])
    def _back_propagate(self, Os, ti):
        gradients = []

        # Output layer
        o = Os[-1] # network output
        print(o)
        o_prev = Os[-2] # output from previous layer
        e = o - ti      
        delta = o * (1 - o) * e
        
        # outer product for batches
        gradients.append(np.einsum("...i,...j->...ij", ddns(o_prev), delta))
        
        # backward loop over hidden layers
        # o starts at second last, o_prev starts at third last, W starts at last weight matrix
        for o, o_prev, W in zip(Os[-2::-1], Os[-3::-1], self.lrs[-1::-1]):           
            # Weight matrix multiplied with delta for batches
            wd = np.einsum("...ij,...j->...i", rmons(W), delta)
            # elementwise multiplication (broadcasting)
            delta = np.einsum("...,...", (o * (1 - o)), wd)
            # outer product for batches
            gradients.append(np.einsum("...i,...j->...ij", ddns(o_prev), delta))
            
        # sum up all batch gradients
        gradients = [np.sum(g, axis=0) for g in reversed(gradients)]
        return gradients
    
    def fit(self, X, y, optimizer, epochs=10, test=None, batch_size=128):
        _, input_dimension = X.shape
        output_dimension = len(np.unique(y))
        self.output_dimension = output_dimension
                
        targets = y
        #self._init_weights(input_dimension, output_dimension)
                
        batch_size = min(len(X), batch_size)
        
        train_history = []
        test_history = []
        
        best_test = best_iteration = 0
        num_batches = int(len(X) / batch_size)
        print("train data size: {} batch size: {} num_batches:{}".format(len(X), batch_size, num_batches))                 
        
        for i in range(epochs):
            permutation = np.random.permutation(range(len(X)))
            k = 0
            for j in range(num_batches):
                    subset = permutation[k:k+batch_size]
                    Os = self.__gtTpts(X[subset])
                    gradients = self._back_propagate(Os, targets[subset])
                    self.lrs = optimizer(self.lrs, gradients, i)
                    k += batch_size


#            score = self.score(X, y)
            train_history.append(score)
            output = "Epoch %d/%d: %2.1fs – training %.5f" % (i + 1, epochs, time() - t, score)
            
#            if test is not None:
#                score = self.score(*test)
#                test_history.append(score)
#                output += " – validation %.5f" % score
                
#                if score > best_test:
#                    best_test = score
#                    best_iteration = i
                
            print(output)
        
        if test is not None:
            print("=> Best validation accuracy was %.5f at iteration %d" % (best_test, best_iteration + 1))
                    
        return train_history, test_history

#Input features size
#Output class size
#Bias
#hidden layers shapes (2x4)(4x2)(2x22)
#neuralNetwork = NrlNtrk(2, 1, 1, [[2,10]])
#neuralNetwork.train(trainSet, trainSetClasses)            
#neuralNetwork.predict(trainSet)

neuralNetwork = NrlNtrk(2, 10, 1, [[784,20]])
neuralNetwork.fit(np.array(X), y, optimizer=GradientDescent(), epochs=30, test=(), batch_size=128)
neuralNetwork.predict(y)


# class input adapter:
    #class init imageVectors.
    # read image.
    # return flattened vector

def train(ftrs, cls):
    return 'manar'
    # while result of network is not cls keep updating weights.
    # updating weights:
        # let first layer calculate ftrs.
        # first layer 
# train
    #inputs: flattened image(train vector), feature
    
#Function takes object
def adaptInput():
    return 'manar'
# predict
    #inputs: 

train data size: 60000 batch size: 128 num_batches:468


TypeError: only integer scalar arrays can be converted to a scalar index

In [ ]:
import numpy as np
import math

from mlxtend.data import loadlocal_mnist

X, y = loadlocal_mnist(
        images_path='images/nn/train-images.idx3-ubyte', 
        labels_path='images/nn/train-labels.idx1-ubyte')
X= X.tolist()
y = y.tolist()
yDecoded = []
for i in y:
    sy = [0 for i in range(0,10)]
    sy[i] = 1
    yDecoded.append(sy)
y = yDecoded


def sigmoid_derivative(p):
    return p * (1 - p)

#file neuralNetwork.py
# input is only normal arrays please.
class NrlNtrk:
    
    def __init__(self, ftrsSz, clsCnt, bias, hdnLrsShps, bp=True):
        self.bp = bp
        self.bias = bias
        self.lrs = [np.random.rand(i[0] + bias, i[1]) for i in hdnLrsShps]
        self.lrs.append(np.random.rand(self.lrs[-1].shape[1] + bias, clsCnt))
        self.__sgmd = lambda x: 1 / (1 + np.e ** -x)
        self.__d = lambda x: x * (1 - x)

    def __rr(self, x, y):
        arr = []
        for i in range (0,len(x)): 
            arr.append( math.pow(y[i]-x[i], 1))
        return np.array(arr, ndmin = 2).T
    
    def __gtTpts(self, ftr):
        tpts = []
        y = np.array(ftr, ndmin=2).T #T here doesn't transpose but get original, because input vector is treated as col.
        for lr in self.lrs:
            tpts.append(self.__sgmd(np.dot(lr.T, y)))
            y = np.array(np.append(tpts[-1], 1), ndmin=2).T 
        return tpts
    def __bpInter(self, rr, tpts, ftr):
        
        ftr = np.array(ftr, ndmin=2).T
        nls = []
        nls.append(self.lrs[1] + np.dot(np.array([np.append(tpts[-2].T, 1)]).T, (2*(rr) * sigmoid_derivative(tpts[-1]))))
        
        for i in range(len(self.lrs)-2, 0, -1):
            nls.append(self.lrs[i] + np.dot(np.array([np.append(tpts[i-1].T, 1)]).T, (2*(rr) * sigmoid_derivative(tpts[i]))))
                
 #       d_weights2 = np.dot(self.layer1.T, (2*(self.y - self.output) * sigmoid_derivative(self.output)))
  #      d_weights1 = np.dot(self.input.T,  (np.dot(2*(self.y - self.output) * sigmoid_derivative(self.output), self.weights2.T) * sigmoid_derivative(self.layer1)))
   
        nls.append(self.lrs[0] + np.dot(ftr,  (np.dot(2*rr * sigmoid_derivative(tpts[-1]), self.lrs[1][:][:-1].T) * sigmoid_derivative(tpts[0]).T)))
        
        self.lrs = list(reversed(nls))
        
    def __bp(self, rr, tpts, ftr):
        cnst = -0.4
        nlrs = []      
        g = rr * tpts[-1] * (1.0 - tpts[-1].T)
        nlrs.append(self.lrs[-1] + (cnst * np.dot(g, np.array(np.append(tpts[-2], 1), ndmin = 2))).T)
        for i in range(len(self.lrs)-2, 0, -1):
            print("Inner layers")
            d = np.diag((tpts[i] * (1 - tpts[i])).T[0])
            g = np.dot(np.dot(d, self.lrs[i+1][:][:-1]), g)
     
            nlrs.append(self.lrs[i] + (cnst * np.dot(g, np.array(np.append(tpts[i-1], 1), ndmin = 2))).T)
        
        d = np.diag((tpts[0] * (1 - tpts[0])).T[0])
        g = np.dot(np.dot(d, self.lrs[1][:][:-1]), g)
        nlrs.append(self.lrs[0] + (cnst * np.dot(g, np.array(ftr, ndmin = 2))).T) 
        
        self.lrs = list(reversed(nlrs))
    def predict(self, ftrs):
        for (x, r) in enumerate(ftrs):
            k = r.copy()
            if(self.bias !=0): k.append(1)
            tpts = self.__gtTpts(k)
            #print("result")
            #print(ftr)
            #print(tpts[-1])
    
    def train(self, ftrs, clsss):
        #move to validation ToDo
        #if isinstance(clsss, np.ndarray) == False:
        #    clsss = np.array(clsss, dtype=float)
        for we in range(0,6250):
            for (x, r) in enumerate(ftrs):
                k = r.copy()
                if(self.bias !=0): k.append(1)
                #Start of numpyfying    
                tpts = self.__gtTpts(k)
                rr = self.__rr(tpts[-1].T, np.array(clsss[x], ndmin=2).T)
                
                print(k)
                print("err")
                print(rr)
                print("Result")
                print(tpts[-1].T)
                print("should")
                print(np.array(clsss[x], ndmin=2).T)
                if(self.bp):
                    self.__bpInter(rr, tpts, k)
                #pdtLrs(tpts, rr)
          #  print(ftrs) 
trainSet = [[1,0],[0,0],[1,1],[0,1]]
trainSetClasses = [[1],[0],[0],[1]]

#Input features size
#Output class size
#Bias
#hidden layers shapes (2x4)(4x2)(2x22)
neuralNetwork = NrlNtrk(2, 1, 1, [[2,10]])
neuralNetwork.train(trainSet, trainSetClasses)            
neuralNetwork.predict(trainSet)


# class input adapter:
    #class init imageVectors.
    # read image.
    # return flattened vector

def train(ftrs, cls):
    return 'manar'
    # while result of network is not cls keep updating weights.
    # updating weights:
        # let first layer calculate ftrs.
        # first layer 
# train
    #inputs: flattened image(train vector), feature
    
#Function takes object
def adaptInput():
    return 'manar'
# predict
    #inputs: 